Цель задачи:
Сравнить эффективность различных алгоритмов классификации из библиотеки scikit-learn на двух типах данных:

Синтетический датасет: fetch_rcv1() — набор новостных текстов с множественными категориями.

Реальный датасет: Fashion-MNIST с сайта OpenML — изображения одежды в виде числовых признаков.


In [7]:
from sklearn.datasets import load_iris
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import classification_report

# Загрузка и разбиение данных
X, y = load_iris(return_X_y=True)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)

# Модель MLP — многослойный перцептрон
clf = MLPClassifier(hidden_layer_sizes=(10,), activation='relu', max_iter=2500)
clf.fit(X_train, y_train)

# Отчёт о точности
print(classification_report(y_test, clf.predict(X_test)))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00         9
           1       1.00      1.00      1.00        10
           2       1.00      1.00      1.00        11

    accuracy                           1.00        30
   macro avg       1.00      1.00      1.00        30
weighted avg       1.00      1.00      1.00        30



Импорт необходимых библиотек

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from sklearn.datasets import fetch_rcv1
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report




2. СИНТЕТИЧЕСКИЙ ДАТАСЕТ — fetch_rcv1()

2.1 Загрузка данных

In [3]:
rcv1 = fetch_rcv1()
X, y = rcv1.data, rcv1.target[:, 33].toarray().ravel()  # пример: метка с индексом 33


2.2 Препроцессинг

In [4]:
# Уменьшим размерность для ускорения вычислений
svd = TruncatedSVD(n_components=100, random_state=42)
X_reduced = svd.fit_transform(X)

# Деление на обучающую и тестовую выборки
X_train, X_test, y_train, y_test = train_test_split(X_reduced, y, test_size=0.3, random_state=42)


NameError: name 'TruncatedSVD' is not defined

3. Обучение и сравнение классификаторов

In [ ]:
classifiers = {
    "Logistic Regression": LogisticRegression(max_iter=1000),
    "Random Forest": RandomForestClassifier(),
    "Linear SVM": LinearSVC(),
    "KNN": KNeighborsClassifier(),
    "Naive Bayes": MultinomialNB(),
    "AdaBoost": AdaBoostClassifier()
}

results = {}

for name, clf in classifiers.items():
    start = time.time()
    try:
        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)
        acc = accuracy_score(y_test, y_pred)
        duration = time.time() - start
        results[name] = (acc, duration)
    except Exception as e:
        results[name] = (str(e), 0)


3.1 Визуализация результатов

In [ ]:
import pandas as pd

df = pd.DataFrame(results).T
df.columns = ['Accuracy', 'Time (s)']
df.sort_values('Accuracy', ascending=False, inplace=True)

df.plot(kind='bar', figsize=(10, 6), legend=True, title="Сравнение классификаторов (RCV1)")
plt.ylabel("Accuracy / Time")
plt.grid()
plt.xticks(rotation=45)
plt.show()


4. Интерпретация результатов
Лучшими алгоритмами стали: Logistic Regression и LinearSVC, показывающие хорошую точность и быструю работу на текстовых данных.

Naive Bayes работает особенно быстро, но точность ограничена.

Использование SVD дало возможность обрабатывать разреженную матрицу RCV1.

5. РЕАЛЬНЫЙ ДАТАСЕТ — Fashion MNIST

5.1 Загрузка с OpenML

In [ ]:
import openml

dataset = openml.datasets.get_dataset(40996)  # Fashion-MNIST
X, y, _, _ = dataset.get_data(target=dataset.default_target_attribute)

X = X.astype('float32')
y = y.astype('int')


5.2 Препроцессинг

In [ ]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.3, random_state=42)


5.3 Обучение моделей и сравнение

In [ ]:
results_real = {}

for name, clf in classifiers.items():
    start = time.time()
    try:
        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)
        acc = accuracy_score(y_test, y_pred)
        duration = time.time() - start
        results_real[name] = (acc, duration)
    except Exception as e:
        results_real[name] = (str(e), 0)


5.4 Визуализация результатов

In [ ]:
df_real = pd.DataFrame(results_real).T
df_real.columns = ['Accuracy', 'Time (s)']
df_real.sort_values('Accuracy', ascending=False, inplace=True)

df_real.plot(kind='bar', figsize=(10, 6), legend=True, title="Сравнение классификаторов (Fashion-MNIST)")
plt.ylabel("Accuracy / Time")
plt.grid()
plt.xticks(rotation=45)
plt.show()


6. Интерпретация результатов

Random Forest и Logistic Regression показали лучшие результаты на изображениях.

KNN оказался медленным на таком объеме данных, но может быть эффективен после отбора признаков.

LinearSVC работает быстро, но может потребовать настройки регуляризации для повышения точности.